In [1]:
import numpy as np
import pandas as pd
import sys
import os
from codebase.file_utils import save_obj, load_obj
from codebase.post_process import samples_to_df, get_post_df
import altair as alt
alt.data_transformers.disable_max_rows()

%load_ext autoreload
%autoreload 2

In [2]:
ppp = True
log_dir = "./log/20211011_183501_ez-exp_s0m3/"
data = load_obj('data', log_dir)


if ppp: 
    ps = load_obj('ps', log_dir)
    ps.keys()
else: 
    print("\n\nChecking data integrity...\n\n")
    complete_data = load_obj("complete_data", log_dir)

    model_posterior_samples = dict()
    model_posterior_samples[0] = load_obj('ps_0', log_dir)
    model_posterior_samples[1] = load_obj('ps_1', log_dir)
    model_posterior_samples[2] = load_obj('ps_2', log_dir)



In [3]:
data

{'random_seed': 0,
 'N': 1000,
 'K': 2,
 'J': 6,
 'alpha': array([0., 0., 0., 0., 0., 0.]),
 'beta': array([[1. , 0. ],
        [0.8, 0. ],
        [0.8, 0. ],
        [0. , 1. ],
        [0. , 0.8],
        [0. , 0.8]]),
 'sigma_z': array([1., 1.]),
 'Phi_corr': array([[1. , 0.2],
        [0.2, 1. ]]),
 'Phi_cov': array([[1. , 0.2],
        [0.2, 1. ]]),
 'z': array([[-1.61951071, -1.11334743],
        [-2.17539248,  0.65913812],
        [-0.8285194 , -2.064689  ],
        ...,
        [-0.21506008, -0.091414  ],
        [-1.18581773, -0.98541301],
        [ 1.7136435 ,  0.05538257]]),
 'y': array([[-4.32504373, -4.38730471, -1.22198053, -2.70652732, -1.01967297,
         -2.03919375],
        [-3.43862813, -2.51570901, -0.59226408,  2.20002122,  1.12333169,
         -1.12253058],
        [ 0.21793111,  0.46024436, -0.22303659, -3.04390179, -0.49471265,
         -0.97153843],
        ...,
        [-2.33686579,  0.15087484, -0.66135544, -2.12297416, -2.8736911 ,
          1.32768299],


In [4]:
print(open(log_dir+'model.txt').read())

data {
  int<lower=1> N;
  int<lower=1> K;
  int<lower=1> J;
  int<lower=0, upper=1> DD[N, J];
}

transformed data{
  vector[K] zeros_K = rep_vector(0, K);
  cov_matrix[K] I_K = diag_matrix(rep_vector(1, K));
}

parameters {
  vector[J] alpha;
  matrix[2,K] beta_free; // 2 free eleements per factor
  cov_matrix [K] Phi_cov;
  matrix[N,K] zz;
}

transformed parameters{
  matrix[J,K] beta;
  matrix[N,J] yy;

  for(j in 1:J) {
    for (k in 1:K) beta[j,k] = 0;
    }

  // set ones
  for (k in 1:K) beta[1+3*(k-1), k] = 1;

  // set the free elements
  for (k in 1:K) beta[2+3*(k-1) : 3+3*(k-1), k] = beta_free[1:2,k];

  for (n in 1:N) yy[n,] = to_row_vector(alpha) + zz[n,] * beta';
}
  
model {
  to_vector(beta_free) ~ normal(0, 1);
  to_vector(alpha) ~ normal(0, 10);
  Phi_cov ~ inv_wishart(J+4, I_K);
  for (n in 1:N) to_vector(zz[n,])  ~ multi_normal(zeros_K, Phi_cov);
  for (j in 1:J) DD[, j] ~ bernoulli_logit(yy[, j]);
  
}



In [5]:
if ppp:
    num_chains = ps['alpha'].shape[1]
    num_samples = ps['alpha'].shape[0]
    for chain_number in range(ps['alpha'].shape[1]):
        for i in range(num_samples):
            sign1 = np.sign(ps['beta'][i,chain_number,0,0])
            sign2 = np.sign(ps['beta'][i,chain_number,3,1])
            ps['beta'][i,chain_number,:3,0] = ps['beta'][i,chain_number,:3,0] * sign1
            ps['beta'][i,chain_number,3:,1] = ps['beta'][i,chain_number,3:,1] * sign2

            if 'Phi_cov' in ps.keys():
                ps['Phi_cov'][i,chain_number,0,1] = sign1 * sign2 * ps['Phi_cov'][i,chain_number,0,1]
                ps['Phi_cov'][i,chain_number,1,0] = ps['Phi_cov'][i,chain_number,0,1]
    
else:
    num_chains = model_posterior_samples[0]['alpha'].shape[1]
    num_samples = model_posterior_samples[0]['alpha'].shape[0]
    for j in range(3):
        ps = model_posterior_samples[j]    
        for chain_number in range(ps['alpha'].shape[1]):
            for i in range(num_samples):
                sign1 = np.sign(ps['beta'][i,chain_number,0,0])
                sign2 = np.sign(ps['beta'][i,chain_number,3,1])
                ps['beta'][i,chain_number,:3,0] = ps['beta'][i,chain_number,:3,0] * sign1
                ps['beta'][i,chain_number,3:,1] = ps['beta'][i,chain_number,3:,1] * sign2

                if 'Phi_cov' in ps.keys():
                    ps['Phi_cov'][i,chain_number,0,1] = sign1 * sign2 * ps['Phi_cov'][i,chain_number,0,1]
                    ps['Phi_cov'][i,chain_number,1,0] = ps['Phi_cov'][i,chain_number,0,1]
        model_posterior_samples[j] = ps



In [6]:
# samples_to_df(model_posterior_samples[0], 'alpha').head()
samples_to_df(ps, 'alpha').head()

index       val param_name  cn  row
0      0  0.022963      alpha   0    0
1      1 -0.009673      alpha   0    0
2      2 -0.097429      alpha   0    0
3      3 -0.003567      alpha   0    0
4      4 -0.105760      alpha   0    0

In [7]:
c1 = alt.Chart(samples_to_df(ps, 'beta')).mark_line(opacity=0.8).encode(
    alt.X('index:O'),
    alt.Y('val'),
    alt.Color('cn:N'),
    row = 'row:O',
    column= 'col:O'
).properties(width = 200, height=100, title='Beta') 

c1.interactive()

alt.Chart(...)

In [8]:
c1 = alt.Chart(samples_to_df(ps, 'alpha')).mark_line(opacity=0.8).encode(
    alt.X('index:O'),
    alt.Y('val'),
    alt.Color('cn:N'),
    row = 'row:O',
    column= 'cn:N'
).properties(width = 200, height=100) 

c1.interactive()

alt.Chart(...)

In [9]:
param = 'beta'
df = get_post_df(ps[param])
df_quant = df.groupby(['row', 'col'])[['value']].quantile(0.025).reset_index()
df_quant.rename({'value':'q1'}, axis=1, inplace=True)
df_quant2 = df.groupby(['row', 'col'])[['value']].quantile(0.975).reset_index()
df_quant2.rename({'value':'q2'}, axis=1, inplace=True)

df = df_quant.merge(df_quant2, on=['row', 'col'])

dd = pd.DataFrame(data['beta'], columns=['0', '1'])
dd['row'] = np.arange(dd.shape[0])
dd = dd.melt(id_vars='row', var_name='col', value_name = 'data')
dd['col'] = dd.col.astype(int)

plot_data = df.merge(dd, on=['row', 'col'])
plot_data['index'] = 'row ' + plot_data.row.astype(str)+' .col '+plot_data.col.astype(str)


c1 = alt.Chart(plot_data).mark_bar(opacity=0.6).encode(
        alt.X('q1', title=None),
        alt.X2('q2', title=None))
c1



c2 = alt.Chart(plot_data).mark_point(opacity=1, color='red').encode(
        alt.X('data', title=None)
)
(c1+c2
).facet(
       'index',
    columns=2
    )

alt.FacetChart(...)

In [10]:
param = 'Phi_cov'
df = get_post_df(ps[param])
df = df[(df.row==0)&(df.col==1)]
df_quant = df.groupby(['row', 'col'])[['value']].quantile(0.025).reset_index()
df_quant.rename({'value':'q1'}, axis=1, inplace=True)
df_quant2 = df.groupby(['row', 'col'])[['value']].quantile(0.975).reset_index()
df_quant2.rename({'value':'q2'}, axis=1, inplace=True)

plot_data = df_quant.merge(df_quant2, on=['row', 'col'])
plot_data['data'] = data['Phi_cov'][0,1]
plot_data
plot_data['index'] = 'row ' + plot_data.row.astype(str)+' .col '+plot_data.col.astype(str)


c1 = alt.Chart(plot_data).mark_bar(opacity=0.6).encode(
        alt.X('q1', title=None),
        alt.X2('q2', title=None))
c1



c2 = alt.Chart(plot_data).mark_point(opacity=1, color='red').encode(
        alt.X('data', title=None)
)
(c1+c2
).facet(
       'index',
    columns=2
    )

alt.FacetChart(...)